This notebook will be used mainly for the Capstone Project for the Applied Data Science course on Coursera.


In [228]:
import pandas as pd
import numpy as np
import math

In [229]:
import requests
from pandas.io.json import json_normalize
import geopandas as gpd
from sklearn.cluster import KMeans
from shapely.geometry import Polygon, LineString, Point
from shapely.ops  import transform

In [230]:
# Matplotlib and associated plotting modules
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
#from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 geopandas=0.4.1 --yes 
import folium # map rendering library

Create a map of Edinburgh, split into its natural neighbourhoods.
https://python-visualization.github.io/folium/quickstart.html This is a link for my use later when I want to colour code the map based on similarity.

In [231]:
url = ("https://opendata.arcgis.com/datasets/4082b44746eb4da8b5935be2d3a00185_27.geojson" #dataset for natural neighbourhoods in Edinburgh from Edinburgh City Council
)
neighbourhoods = gpd.read_file(url)
print(neighbourhoods.head())

   OBJECTID             NATURALCOM  OID_  CNT_NATURA  DUMMY_  SUM_ELECNO  \
0         1  Brunstane/Gilberstoun  1485        1485    1485     1485.30   
1         2           Newcraighall   262         262     262      261.77   
2         3              Magdalene  1479        1479    1479     1478.53   
3         4              Newbridge   327         327     327      326.84   
4         5     Cammo/Strathalmond   874         874     874      873.59   

   Z009_ELEC     Shapearea      Shapelen  \
0       1485  1.147451e+06   4629.409487   
1        262  4.414281e+05   3515.734273   
2       1479  3.119711e+05   2590.027278   
3        327  5.567828e+06  11661.263206   
4        874  2.008664e+06   7150.150690   

                                            geometry  
0  POLYGON ((-3.10276 55.94435, -3.10276 55.94435...  
1  MULTIPOLYGON (((-3.09979 55.93598, -3.09855 55...  
2  POLYGON ((-3.10240 55.94088, -3.10245 55.94165...  
3  POLYGON ((-3.41296 55.95159, -3.41414 55.95153...  
4  

In [232]:
url = (
    "https://opendata.arcgis.com/datasets/4082b44746eb4da8b5935be2d3a00185_27.geojson" #dataset for natural neighbourhoods in Edinburgh from Edinburgh City Council
)
natural_neighbourhoods = f"{url}"


m = folium.Map(
    location=[55.9533, -3.1883],
    tiles="cartodbpositron",
    zoom_start=13,
)

shapes = folium.GeoJson(natural_neighbourhoods, name="geojson")

shapes.add_to(m)
    
folium.LayerControl().add_to(m)

m

https://geopandas.readthedocs.io/en/latest/gallery/polygon_plotting_with_folium.html example I used to help with the next cell.

In [233]:
path = "https://opendata.arcgis.com/datasets/4082b44746eb4da8b5935be2d3a00185_27.geojson"
df = gpd.read_file(path)

m = folium.Map(location=[55.9533, -3.1883], zoom_start=10, tiles='CartoDB positron')

for _, r in df.iterrows():
    #without simplifying the representation of each borough, the map might not be displayed
    sim_geo = gpd.GeoSeries(r['geometry'])
    #sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'orange'})
    folium.Popup(r['NATURALCOM']).add_to(geo_j)
    geo_j.add_to(m)

df = df.to_crs(epsg=2163) #set to a projected crs for centroid calculation accuracy.
df['centroids']=df.centroid.to_crs(epsg=4326)
df['lat'] = df['centroids'].y
df['lon'] = df['centroids'].x
df = df.to_crs(epsg=4326)

for _, r in df.iterrows():
    yo = folium.Marker(location=[r['lat'], r['lon']], popup='name: {}'.format(r['NATURALCOM']))
    yo.add_to(m)
print(df)
m

     OBJECTID                 NATURALCOM  OID_  CNT_NATURA  DUMMY_  \
0           1      Brunstane/Gilberstoun  1485        1485    1485   
1           2               Newcraighall   262         262     262   
2           3                  Magdalene  1479        1479    1479   
3           4                  Newbridge   327         327     327   
4           5         Cammo/Strathalmond   874         874     874   
..        ...                        ...   ...         ...     ...   
149       150    Corstorphine/Craigmount  9799        9799    9799   
150       151               Corstorphine  9799        9799    9799   
151       152      Corstorphine/Clerwood  9799        9799    9799   
152       153  The Christians/Portobello  3535        3535    3535   
153       154      Ferryfield/Inverleith  3228        3228    3228   

     SUM_ELECNO  Z009_ELEC     Shapearea      Shapelen  \
0       1485.30       1485  1.147451e+06   4629.409487   
1        261.77        262  4.414281e+05   

In [234]:
CLIENT_ID = "K0K1215GLOMPN31CWAJTTG2MEXDNRZ2UJ1B1PYU0DXCCI3QZ"
CLIENT_SECRET = "E2ROHURCBVBBDLKJQ0MA4L0LQCSXYXLQJFZWVF0QAN3OJMHD"
VERSION = '20180605'
LIMIT = 100

In [235]:


def getNearbyVenues(names, latitudes, longitudes, area):
    
    venues_list=[]
    for name, lat, lng, area2 in zip(names, latitudes, longitudes, area):
        
        radius = 2*math.sqrt(area2/3) #factor of two to account for weirdly shaped areas. This makes a circle with twice the radius of the circle of the same area as the shape.
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId=4d4b7105d754a06374d81259'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng,
            radius,
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['venues']
        #print(results)
        
        # return only relevant information for each nearby venue
        venues_list.append([[name, lat, lng, v['id'],v['name'], v['location']['lat'], v['location']['lng'], v['categories'][0]['name']] for v in results])
        
        
            

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude',
                  'Venue ID',
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [236]:
edinburgh_venues = getNearbyVenues(names=df['NATURALCOM'],
                                   latitudes=df['lat'],
                                   longitudes=df['lon'],
                                   area = df['Shapearea']
                                  )
edinburgh_venues.head()

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Brunstane/Gilberstoun               55.940545                 -3.09246   
1  Brunstane/Gilberstoun               55.940545                 -3.09246   
2  Brunstane/Gilberstoun               55.940545                 -3.09246   
3  Brunstane/Gilberstoun               55.940545                 -3.09246   
4  Brunstane/Gilberstoun               55.940545                 -3.09246   

                   Venue ID             Venue  Venue Latitude  \
0  54b97471498e26d1ad55ee73          Bar Zest       55.944542   
1  4c4c67949e6dbe9a15c9700d  Porto Restaurant       55.946333   
2  55f5ab5b498e2e9e358c41ee       Burger King       55.932062   
3  4c417b3aaf052d7fd7707d79       Cuddie Brae       55.934582   
4  5e2106cce7117a0008c0689b          wagamama       55.935084   

   Venue Longitude        Venue Category  
0        -3.096077             Gastropub  
1        -3.084878  Fast Food Restaurant  
2        -3.104912  Fast Food Restaurant  
3        -3.094717            Restaurant  
4        -3.104329            Restaurant

Next I need to clean up the dataframe to take out venues that are not inside the neighbourhood boundaries.

In [237]:
edinburgh_venues_geo = gpd.GeoDataFrame(edinburgh_venues, geometry = gpd.points_from_xy(edinburgh_venues["Venue Longitude"],edinburgh_venues["Venue Latitude"]))
edinburgh_venues_geo.head()


Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Brunstane/Gilberstoun               55.940545                 -3.09246   
1  Brunstane/Gilberstoun               55.940545                 -3.09246   
2  Brunstane/Gilberstoun               55.940545                 -3.09246   
3  Brunstane/Gilberstoun               55.940545                 -3.09246   
4  Brunstane/Gilberstoun               55.940545                 -3.09246   

                   Venue ID             Venue  Venue Latitude  \
0  54b97471498e26d1ad55ee73          Bar Zest       55.944542   
1  4c4c67949e6dbe9a15c9700d  Porto Restaurant       55.946333   
2  55f5ab5b498e2e9e358c41ee       Burger King       55.932062   
3  4c417b3aaf052d7fd7707d79       Cuddie Brae       55.934582   
4  5e2106cce7117a0008c0689b          wagamama       55.935084   

   Venue Longitude        Venue Category                   geometry  
0        -3.096077             Gastropub  POINT (-3.09608 55.94454)  
1        -3.084878  Fast Food Restaurant  POINT (-3.08488 55.94633)  
2        -3.104912  Fast Food Restaurant  POINT (-3.10491 55.93206)  
3        -3.094717            Restaurant  POINT (-3.09472 55.93458)  
4        -3.104329            Restaurant  POINT (-3.10433 55.93508)

Define a function to find which neighbourhood the venue is really in.

In [238]:
def which_neighbourhood(test_point):
    for i in range(154):
        if df["geometry"].contains(test_point)[i] == True:
            return df["NATURALCOM"][i]

Run the function for every row of the data frame and drop any rows where the neighbourhood label is not accurate in terms of the natural neighbourhood boundary.

In [239]:
print(edinburgh_venues_geo.shape)
for ind in edinburgh_venues_geo.index:
    location = edinburgh_venues_geo['geometry'][ind]
    if edinburgh_venues_geo['Neighbourhood'][ind] != which_neighbourhood(location):
        edinburgh_venues_geo.drop(ind, inplace = True)
edinburgh_venues_geo.reset_index(inplace = True)
edinburgh_venues_geo.drop(["index"], axis=1, inplace = True)
print(edinburgh_venues_geo.shape)
edinburgh_venues_geo.head()

(4803, 9)
(821, 9)


Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Brunstane/Gilberstoun               55.940545                 -3.09246   
1  Brunstane/Gilberstoun               55.940545                 -3.09246   
2  Brunstane/Gilberstoun               55.940545                 -3.09246   
3  Brunstane/Gilberstoun               55.940545                 -3.09246   
4  Brunstane/Gilberstoun               55.940545                 -3.09246   

                   Venue ID                  Venue  Venue Latitude  \
0  54b97471498e26d1ad55ee73               Bar Zest       55.944542   
1  5ecfd256fadd010008813b03           Costa Coffee       55.941996   
2  4e0cd9d27d8bfe35bbc5d23d  eh15 Restaurant & Bar       55.943865   
3  4cdd6bd114119eb02a35ed33            Burger King       55.942378   
4  4e0b733ab0fbc7fb0be0d383                Options       55.944675   

   Venue Longitude        Venue Category                   geometry  
0        -3.096077             Gastropub  POINT (-3.09608 55.94454)  
1        -3.101744           Coffee Shop  POINT (-3.10174 55.94200)  
2        -3.098488                 Diner  POINT (-3.09849 55.94386)  
3        -3.101092  Fast Food Restaurant  POINT (-3.10109 55.94238)  
4        -3.096049            Restaurant  POINT (-3.09605 55.94467)

Map all venues that are still being used.

In [240]:
m = folium.Map(location=[55.9533, -3.1883], zoom_start=10, tiles='CartoDB positron')

for _, r in df.iterrows():
    sim_geo = gpd.GeoSeries(r['geometry'])
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'orange'})
    folium.Popup(r['NATURALCOM']).add_to(geo_j)
    geo_j.add_to(m)

for _, r in edinburgh_venues_geo.iterrows():
    yo = folium.Marker(location=[r['Venue Latitude'], r['Venue Longitude']], popup='name: {}'.format(r['Venue']))
    yo.add_to(m)
m

Now to add a column with additional data about each venue.

In [241]:
#returns the price tier and likes count of the venues.

def furtherDetails(venue_id):
    url = 'https://api.foursquare.com/v2/venues/{}?&client_id={}&client_secret={}&v={}'.format(venue_id,CLIENT_ID, CLIENT_SECRET,VERSION)
    results = requests.get(url).json()
    try:
        return results['response']['venue']['attributes']['groups'][0]['items'][0]['priceTier'], results['response']['venue']['likes']['count']
    except:
        return "oops!", "oh no!" #if the data is strangely formatted for this venue.
#venue_id = '54b97471498e26d1ad55ee73'

#url = 'https://api.foursquare.com/v2/venues/{}?&client_id={}&client_secret={}&v={}'.format(venue_id,CLIENT_ID, CLIENT_SECRET,VERSION)
    
#results = requests.get(url).json()
#print(results['response']['venue']['attributes']['groups'][0]['items'][0]['priceTier']) #finds the price tier of the venue.
#print(results['response']['venue']['likes']['count']) #returns the likes count for the venue
#print(results['response']['venue'])

In [256]:
edinburgh_venues_geo['price tier','likes'] = edinburgh_venues_geo['Venue ID'].apply(furtherDetails) #change this to two columns another day when have more premium calls. 
edinburgh_venues_geo.head()
#edinburgh_venues_geo['price tier'] = edinburgh_venues_geo['price tier','likes'][0]
#edinburgh_venues_geo['price tier'] = 0
#edinburgh_venues_geo['likes'] = edinburgh_venues_geo['price tier','likes'][1]

edinburgh_venues_geo.head()
#TAKE OUT ANY ROWS WITH OOPS! OR OH NO!


Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
1  Brunstane/Gilberstoun               55.940545                -3.092460   
2  Brunstane/Gilberstoun               55.940545                -3.092460   
3  Brunstane/Gilberstoun               55.940545                -3.092460   
4  Brunstane/Gilberstoun               55.940545                -3.092460   
5           Newcraighall               55.934650                -3.088188   

                   Venue ID                  Venue  Venue Latitude  \
1  5ecfd256fadd010008813b03           Costa Coffee       55.941996   
2  4e0cd9d27d8bfe35bbc5d23d  eh15 Restaurant & Bar       55.943865   
3  4cdd6bd114119eb02a35ed33            Burger King       55.942378   
4  4e0b733ab0fbc7fb0be0d383                Options       55.944675   
5  4c417b3aaf052d7fd7707d79            Cuddie Brae       55.934582   

   Venue Longitude        Venue Category                   geometry  \
1        -3.101744           Coffee Shop  POINT (-3.10174 55.94200)   
2        -3.098488                 Diner  POINT (-3.09849 55.94386)   
3        -3.101092  Fast Food Restaurant  POINT (-3.10109 55.94238)   
4        -3.096049            Restaurant  POINT (-3.09605 55.94467)   
5        -3.094717            Restaurant  POINT (-3.09472 55.93458)   

  (price tier, likes)  price tier  likes  
1     (oops!, oh no!)           0      0  
2     (oops!, oh no!)           0      0  
3     (oops!, oh no!)           0      0  
4     (oops!, oh no!)           0      0  
5     (oops!, oh no!)           0      0

In [260]:
edinburgh_venues_geo['price tier'] = [edinburgh_venues_geo['price tier','likes'][0]]
edinburgh_venues_geo['likes'] = [edinburgh_venues_geo['price tier','likes'][1]]

KeyError: 0

In [ ]:
###DRAFT

for i in range(edinburgh_venues_geo.shape[0]):
    edinburgh_venues_geo['price tier'][i] = edinburgh_venues_geo['price tier','likes'][i][0]
    edinburgh_venues_geo['likes'][i] = edinburgh_venues_geo['price tier','likes'][i][1]
    if edinburgh_venues_geo['price tier'][i] == "oops!":
        edinburgh_venues_geo.drop([i], inplace = True)
    #if edinburgh_venues_geo['likes'][i] == "oh no!": ONLY NEED ONE OF TWO
     #   edinburgh_venues_geo.drop([i], axis=0, inplace = True)
print(edinburgh_venues_geo.shape)
edinburgh_venues_geo.head()

Use get_dummies to say which type of venue each venue is.

In [243]:
edin_onehot = pd.get_dummies(edinburgh_venues_geo['Venue Category'])
#, prefix="", prefix_sep=""
print(edin_onehot)
edin_onehot['likes'] = edinburgh_venues_geo['likes']
#Move the Neighbourhood column to the start.
fixed_columns = [edin_onehot.columns[-1]] + list(edin_onehot.columns[:-1])
edin_onehot = edin_onehot[fixed_columns]
edin_onehot['Neighbourhood'] = edinburgh_venues_geo['Neighbourhood']
fixed_columns = [edin_onehot.columns[-1]] + list(edin_onehot.columns[:-1])
edin_onehot = edin_onehot[fixed_columns]
edin_onehot.head(20)


     African Restaurant  American Restaurant  Arcade  Asian Restaurant  \
1                     0                    0       0                 0   
2                     0                    0       0                 0   
3                     0                    0       0                 0   
4                     0                    0       0                 0   
5                     0                    0       0                 0   
..                  ...                  ...     ...               ...   
816                   0                    0       0                 0   
817                   0                    0       0                 0   
818                   0                    0       0                 0   
819                   0                    0       0                 0   
820                   0                    0       0                 0   

     BBQ Joint  Bagel Shop  Bakery  Bar  Beach Bar  Beer Bar  ...  Steakhouse  \
1            0           0    

Neighbourhood likes  African Restaurant  American Restaurant  \
1   Brunstane/Gilberstoun     0                   0                    0   
2   Brunstane/Gilberstoun     0                   0                    0   
3   Brunstane/Gilberstoun     0                   0                    0   
4   Brunstane/Gilberstoun     0                   0                    0   
5            Newcraighall     0                   0                    0   
6               Magdalene     0                   0                    0   
7               Magdalene     0                   0                    0   
8               Newbridge     0                   0                    0   
9               Newbridge     0                   0                    0   
10              Newbridge     0                   0                    0   
11              Newbridge     0                   0                    0   
12              Newbridge     0                   0                    0   
13              Newbridge     0                   0                    0   
14              Muirhouse     0                   0                    0   
15              Muirhouse     0                   0                    0   
16              Muirhouse     0                   0                    0   
17              Muirhouse     0                   0                    0   
18              Muirhouse     0                   0                    0   
19    Granton/West Pilton     0                   0                    0   
20    Granton/West Pilton     0                   0                    0   

    Arcade  Asian Restaurant  BBQ Joint  Bagel Shop  Bakery  Bar  ...  \
1        0                 0          0           0       0    0  ...   
2        0                 0          0           0       0    0  ...   
3        0                 0          0           0       0    0  ...   
4        0                 0          0           0       0    0  ...   
5        0                 0          0           0       0    0  ...   
6        0                 0          0           0       0    0  ...   
7        0                 0          0           0       0    0  ...   
8        0                 0          0           0       0    0  ...   
9        0                 0          0           0       0    0  ...   
10       0                 0          0           0       0    0  ...   
11       0                 0          0           0       1    0  ...   
12       0                 0          0           0       0    0  ...   
13       0                 0          0           0       1    0  ...   
14       0                 0          0           0       1    0  ...   
15       0                 0          0           0       0    0  ...   
16       0                 0          0           0       0    0  ...   
17       0                 0          0           0       0    0  ...   
18       0                 0          0           0       0    0  ...   
19       0                 0          0           0       0    0  ...   
20       0                 0          0           0       0    0  ...   

    Steakhouse  Sushi Restaurant  Taco Place  Tea Room  Thai Restaurant  \
1            0                 0           0         0                0   
2            0                 0           0         0                0   
3            0                 0           0         0                0   
4            0                 0           0         0                0   
5            0                 0           0         0                0   
6            0                 0           0         0                0   
7            0                 0           0         0                0   
8            0                 0           0         0                0   
9            0                 0           0         0                0   
10           0                 0           0         0                0   
11           0                 0           0         0  

Weight the restaurant choices by the number of likes unless the number of likes is 0.
This is done by using the original onehot df * the likes plus the original onehot df.
More popular places become more important in the analysis.

In [248]:
edin_weighted = edin_onehot.iloc[:,2:].mul(edin_onehot.iloc[:,1], axis=0) + edin_onehot.iloc[:,2:]
edin_weighted['Neighbourhood'] = edinburgh_venues_geo['Neighbourhood']
fixed_columns = [edin_weighted.columns[-1]] + list(edin_weighted.columns[:-1])
edin_weighted = edin_weighted[fixed_columns]
edin_weighted["price"] = edinburgh_venues_geo['price tier']
print(edin_weighted.shape)
edin_weighted.head(20)

(820, 90)


Neighbourhood African Restaurant American Restaurant Arcade  \
1   Brunstane/Gilberstoun                  0                   0      0   
2   Brunstane/Gilberstoun                  0                   0      0   
3   Brunstane/Gilberstoun                  0                   0      0   
4   Brunstane/Gilberstoun                  0                   0      0   
5            Newcraighall                  0                   0      0   
6               Magdalene                  0                   0      0   
7               Magdalene                  0                   0      0   
8               Newbridge                  0                   0      0   
9               Newbridge                  0                   0      0   
10              Newbridge                  0                   0      0   
11              Newbridge                  0                   0      0   
12              Newbridge                  0                   0      0   
13              Newbridge                  0                   0      0   
14              Muirhouse                  0                   0      0   
15              Muirhouse                  0                   0      0   
16              Muirhouse                  0                   0      0   
17              Muirhouse                  0                   0      0   
18              Muirhouse                  0                   0      0   
19    Granton/West Pilton                  0                   0      0   
20    Granton/West Pilton                  0                   0      0   

   Asian Restaurant BBQ Joint Bagel Shop Bakery Bar Beach Bar  ...  \
1                 0         0          0      0   0         0  ...   
2                 0         0          0      0   0         0  ...   
3                 0         0          0      0   0         0  ...   
4                 0         0          0      0   0         0  ...   
5                 0         0          0      0   0         0  ...   
6                 0         0          0      0   0         0  ...   
7                 0         0          0      0   0         0  ...   
8                 0         0          0      0   0         0  ...   
9                 0         0          0      0   0         0  ...   
10                0         0          0      0   0         0  ...   
11                0         0          0      1   0         0  ...   
12                0         0          0      0   0         0  ...   
13                0         0          0      1   0         0  ...   
14                0         0          0      1   0         0  ...   
15                0         0          0      0   0         0  ...   
16                0         0          0      0   0         0  ...   
17                0         0          0      0   0         0  ...   
18                0         0          0      0   0         0  ...   
19                0         0          0      0   0         0  ...   
20                0         0          0      0   0         0  ...   

   Sushi Restaurant Taco Place Tea Room Thai Restaurant Turkish Restaurant  \
1                 0          0        0               0                  0   
2                 0          0        0               0                  0   
3                 0          0        0               0                  0   
4                 0          0        0               0                  0   
5                 0          0        0               0                  0   
6                 0          0        0               0                  0   
7                 0          0        0               0                  0   
8                 0          0        0               0                  0   
9                 0          0        0               0                  0   
10                0          0        0               0                  0   
11                0          0        0               0                  0   
12                0          

Find the proportion of each type of venue.

In [249]:
summed = edin_weighted.sum().drop(["Neighbourhood"])

print(summed.shape)

list_to_use = ["Neighbourhood"]

for i in range(len(summed)):
    if summed[i]>3:
        list_to_use.append(edin_weighted.columns[i+1])
list_to_use

(89,)


['Neighbourhood',
 'BBQ Joint',
 'Bakery',
 'Bar',
 'Bistro',
 'Breakfast Spot',
 'Burger Joint',
 'Cafeteria',
 'Café',
 'Chinese Restaurant',
 'Coffee Shop',
 'Deli / Bodega',
 'Diner',
 'Donut Shop',
 'English Restaurant',
 'Fast Food Restaurant',
 'Fish & Chips Shop',
 'Food Truck',
 'French Restaurant',
 'Gastropub',
 'Ice Cream Shop',
 'Indian Restaurant',
 'Italian Restaurant',
 'Mexican Restaurant',
 'Pizza Place',
 'Pub',
 'Restaurant',
 'Sandwich Place',
 'Scottish Restaurant',
 'Seafood Restaurant',
 'Snack Place',
 'Steakhouse',
 'Sushi Restaurant',
 'Tea Room',
 'Vietnamese Restaurant']

In [250]:
print(edin_weighted.head())

#.reset_index()
edin_grouped = edin_weighted.groupby('Neighbourhood').mean()
#edin_grouped = edin_grouped[list_to_use]
#print(edin_grouped.shape)
edin_grouped.head()

           Neighbourhood African Restaurant American Restaurant Arcade  \
1  Brunstane/Gilberstoun                  0                   0      0   
2  Brunstane/Gilberstoun                  0                   0      0   
3  Brunstane/Gilberstoun                  0                   0      0   
4  Brunstane/Gilberstoun                  0                   0      0   
5           Newcraighall                  0                   0      0   

  Asian Restaurant BBQ Joint Bagel Shop Bakery Bar Beach Bar  ...  \
1                0         0          0      0   0         0  ...   
2                0         0          0      0   0         0  ...   
3                0         0          0      0   0         0  ...   
4                0         0          0      0   0         0  ...   
5                0         0          0      0   0         0  ...   

  Sushi Restaurant Taco Place Tea Room Thai Restaurant Turkish Restaurant  \
1                0          0        0               0         

DataError: No numeric types to aggregate

In [199]:
num_top_venues = 3

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighbourhoods_venues_sorted = pd.DataFrame(columns=columns)
neighbourhoods_venues_sorted['Neighbourhood'] = edin_grouped['Neighbourhood']

for ind in np.arange(edin_grouped.shape[0]):
    neighbourhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(edin_grouped.iloc[ind, :], num_top_venues)
    
neighbourhoods_venues_sorted.head()


Neighbourhood 1st Most Common Venue 2nd Most Common Venue  \
0              Abbeyhill    Chinese Restaurant                  Café   
1               Baberton     Fish & Chips Shop                 price   
2                Balerno             Gastropub                  Café   
3  Balgreen/Saughtonhall        Ice Cream Shop     Indian Restaurant   
4               Bankhead                Bakery  Fast Food Restaurant   

   3rd Most Common Venue  
0  Vietnamese Restaurant  
1             Donut Shop  
2      Indian Restaurant  
3             Restaurant  
4              Gastropub

Create a density measure 

In [148]:
edinburgh_venues_geo["Venue count"]=1
edinburgh_venues_count = edinburgh_venues_geo.groupby('Neighbourhood').sum().reset_index()
edinburgh_venues_count = edinburgh_venues_count[["Neighbourhood", "Venue count"]]


edinburgh_venues_count = edinburgh_venues_count.join(df.set_index('NATURALCOM'), on='Neighbourhood')

edinburgh_venues_count["Number density"] = edinburgh_venues_count["Venue count"]*10000/edinburgh_venues_count["Shapearea"]


neighbourhoods_venues_sorted["Number density"] = edinburgh_venues_count["Number density"]
print(neighbourhoods_venues_sorted)

             Neighbourhood 1st Most Common Venue 2nd Most Common Venue  \
0                Abbeyhill    Chinese Restaurant                  Café   
1                 Baberton     Fish & Chips Shop    Chinese Restaurant   
2                  Balerno             Gastropub     Indian Restaurant   
3    Balgreen/Saughtonhall            Restaurant        Ice Cream Shop   
4                 Bankhead                Bakery  Fast Food Restaurant   
..                     ...                   ...                   ...   
122                Trinity                  Café            Restaurant   
123              Viewforth                  Café    Chinese Restaurant   
124               West End           Coffee Shop            Restaurant   
125          Wester Hailes                Bakery      Sushi Restaurant   
126             Willowbrae                   Pub                 price   

    3rd Most Common Venue  Number density  
0    Fast Food Restaurant        0.441375  
1    Fast Food Restaura

In [149]:
# set number of clusters
kclusters = 15

edin_grouped_clustering = edin_grouped.drop(['Neighbourhood'], 1)
edin_grouped_clustering["number_density"] = neighbourhoods_venues_sorted["Number density"]

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=1).fit(edin_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([ 4,  7,  9,  9,  9,  9, 14,  8,  9, 14], dtype=int32)

In [150]:
# add clustering labels
neighbourhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
edin_merged = df[['NATURALCOM','lat','lon','geometry']]

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
edin_merged = edin_merged.join(neighbourhoods_venues_sorted.set_index('Neighbourhood'), on='NATURALCOM')

print(edin_merged)
edin_merged.head(20) # check the last columns!


#print(edin_merged.shape)
edin_merged.dropna(axis=0, how='any', thresh=None, subset=None, inplace=True)

                    NATURALCOM        lat       lon  \
0        Brunstane/Gilberstoun  55.940545 -3.092460   
1                 Newcraighall  55.934650 -3.088188   
2                    Magdalene  55.942010 -3.108687   
3                    Newbridge  55.939694 -3.421174   
4           Cammo/Strathalmond  55.958395 -3.324203   
..                         ...        ...       ...   
149    Corstorphine/Craigmount  55.948396 -3.299799   
150               Corstorphine  55.942325 -3.282735   
151      Corstorphine/Clerwood  55.950484 -3.280013   
152  The Christians/Portobello  55.945476 -3.106248   
153      Ferryfield/Inverleith  55.970581 -3.224060   

                                              geometry  Cluster Labels  \
0    POLYGON ((-3.10276 55.94435, -3.10276 55.94435...             0.0   
1    MULTIPOLYGON (((-3.09979 55.93598, -3.09855 55...             2.0   
2    POLYGON ((-3.10240 55.94088, -3.10245 55.94165...             0.0   
3    POLYGON ((-3.41296 55.95159, -3.41414 

In [151]:
# create map
map_clusters = folium.Map(location=[55.9533, -3.1883], zoom_start=10, tiles='CartoDB positron')

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.tab20(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# set colour scheme for neighbourhoods
#colors_array2 = cm.coolwarm(np.linspace(0, 1,120))
#colourscheme = [colors.rgb2hex(i) for i in colors_array2]

# add markers to the map
for lat, lon, poi, cluster, top1, top2, top3, sim_geo, density in zip(edin_merged['lat'], edin_merged['lon'], edin_merged['NATURALCOM'], edin_merged['Cluster Labels'], edin_merged['1st Most Common Venue'],edin_merged['2nd Most Common Venue'],edin_merged['3rd Most Common Venue'],edin_merged['geometry'],edin_merged['Number density']):
    
    geo_j = gpd.GeoSeries(sim_geo).to_json()
    style = {'fillColor': '#fcbbf6','fillOpacity': 0.2, 'color': '#fcbbf6', 'opacity':0.4}
    geo_j = folium.GeoJson(data=geo_j, style_function = lambda x: style)
    folium.Popup(poi).add_to(geo_j)
    geo_j.add_to(map_clusters)
    label = folium.Popup(str(poi) +'-------' + ' Cluster ' + str(cluster) + '-------' + '\n Top venue categories: ' + '\n'+ str(top1) + '\n'+ str(top2) + '\n'+ str(top3), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster-1)],
        fill=True,
        fill_color=rainbow[int(cluster-1)],
        fill_opacity=0.7).add_to(map_clusters)
#folium.LayerControl().add_to(map_clusters)
        
map_clusters

#geopandas.GeoSeries([shapely_polygon]).to_json()

In [80]:
edin_merged[edin_merged["NATURALCOM"].str.contains("Leith")]

NATURALCOM        lat       lon  \
68   Leith/Easter Rd  55.964204 -3.170005   
112            Leith  55.978887 -3.168427   
113      Leith Links  55.967706 -3.157673   

                                              geometry  Cluster Labels  \
68   POLYGON ((-3.17296 55.96908, -3.17297 55.96908...             2.0   
112  POLYGON ((-3.18168 55.99236, -3.18609 55.99082...             4.0   
113  POLYGON ((-3.16618 55.96763, -3.16591 55.96743...             2.0   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
68                 Bakery     Indian Restaurant    Italian Restaurant   
112                  Café    Seafood Restaurant                Bakery   
113    Chinese Restaurant  Fast Food Restaurant     Indian Restaurant   

     Number density  
68         0.164817  
112        0.020642  
113        0.080666